In [92]:

import os

import utils
import pandas as pd
from collections import defaultdict
import numpy as np
from tqdm import tqdm
import asyncio
import plotly.express as px 
import plotly.graph_objects as go
import statsmodels.formula.api as smf
import sqlite3
import os
%autoawait asyncio


In [91]:
BTC_TO_SAT = 10**8
MILLION = 10**6

In [51]:
# Loading the balances database
# The database contains two tables:
# - transactions, which contains the incoming and outgoing transaction amounts for each owner_uuid (incoming have positive amounts, outgoing have negative amounts)
# - btc_price, which contains the daily price of BTC
connection = sqlite3.connect('/Users/gchebi/data/balances_v2.db')
cursor = connection.cursor()

# How many btcs are in muun wallets?


In [61]:
dates = [str(elem) for elem in pd.date_range('2019-01-01','2024-04-01' , freq='1ME')-pd.offsets.MonthBegin(1)]
btcs = []
for date in tqdm(dates):
    query = f'''        
        select sum(amount_in_sat)
        from transactions  
        where date(timestamp) < '{date}'
        and owner_uuid != '' 
'''
    cursor.execute(query)
    res = cursor.fetchall()
    btcs.append(res[0][0]/BTC_TO_SAT)

100%|██████████| 63/63 [00:46<00:00,  1.36it/s] 


In [62]:
fig = px.line(x=dates, y=btcs)
fig.update_layout(xaxis_title="Date", yaxis_title="Number of bitcoins under Muun wallets", template='plotly_white')


# How many usds are in muun wallets? 

In [67]:
prices = []
for date in tqdm(dates):
    query = f'''        
        select price
        from btc_price
        where date(timestamp) = date('{date}') 
'''
    cursor.execute(query)
    res = cursor.fetchall()
    prices.append(res[0][0])

100%|██████████| 63/63 [00:00<00:00, 2241.59it/s]


In [68]:
usds = [btc * price / MILLION for btc,price in zip(btcs, prices)]
fig = px.line(x=dates, y=usds)
fig.update_layout(xaxis_title="Date", yaxis_title="USD under Muun wallets (in millions)", template='plotly_white')


# Balance by users

In [154]:
query = '''
select owner_uuid, sum(amount_in_sat) as balance
from transactions
where owner_uuid != ''
group by 1
'''
cursor.execute(query)
results = cursor.fetchall()

In [155]:
# Min number of sats to be considered
MIN_AMOUNT_IN_SAT = 50000

balance_by_user_df = pd.DataFrame(results, columns = ['owner_uuid', 'balance'])
balance_by_user_df = balance_by_user_df.query(F'balance > {MIN_AMOUNT_IN_SAT}')
balance_by_user_df['balance'] = (balance_by_user_df['balance'] / BTC_TO_SAT).clip(upper=0.5)
fig = px.histogram(balance_by_user_df, x='balance')
fig.update_layout(xaxis_title="Number of held BTCs by user (clipped at 0.5)", yaxis_title="Number of users", template='plotly_white')



In [100]:
# Evolution over time
dates = [str(elem) for elem in pd.date_range('2021-01-01','2024-04-01' , freq='1ME')-pd.offsets.MonthBegin(1)]
quantiles = [0.25, 0.5, 0.75, 0.9, 0.95, 0.99, 0.999]
results = defaultdict(lambda: [])
for date in tqdm(dates):
    query = f'''
        select owner_uuid, sum(amount_in_sat) as balance
        from transactions
        where owner_uuid != ''
        and date(timestamp) < date('{date}')
        group by 1
    '''
    cursor.execute(query)
    query_res = cursor.fetchall()
    df = pd.DataFrame(query_res, columns = ['owner_uuid', 'balance'])
    df = df.query(f'balance > {MIN_AMOUNT_IN_SAT}')
    df['balance'] = df['balance'] / BTC_TO_SAT
    for q in quantiles:
        results[f'quantile_{q}'].append(np.quantile(df['balance'], q))
    
    
    



100%|██████████| 39/39 [11:05<00:00, 17.06s/it]


In [113]:
quantiles_to_plot = [0.25, 0.5, 0.75, 0.9, 0.95, 0.99]
res = pd.DataFrame(results, index=dates)
res.to_csv('account_quantiles.csv')
fig = px.line(res[[f'quantile_{q}' for q in quantiles_to_plot]])
fig.update_layout(xaxis_title="Date", yaxis_title="Number of held BTCs by user", template='plotly_white')

In [114]:
quantiles_to_plot = [0.99, 0.999]
fig = px.line(res[[f'quantile_{q}' for q in quantiles_to_plot]])
fig.update_layout(xaxis_title="Date", yaxis_title="Number of held BTCs by user", template='plotly_white')

In [115]:
quantiles_to_plot = [0.25, 0.5, 0.75]
fig = px.line(res[[f'quantile_{q}' for q in quantiles_to_plot]])
fig.update_layout(xaxis_title="Date", yaxis_title="Number of held BTCs by user", template='plotly_white')

In [ ]:
# How much time are users holding their btcs?

In [144]:
query = f'''
with outputs_w_rn as(
    select *,
           row_number() over (partition by owner_uuid, amount_in_sat order by timestamp) as rn
    from transactions
    where amount_in_sat > 0
    and owner_uuid != ''
),

    inputs_w_rn as(
    select *,
           row_number() over (partition by owner_uuid, amount_in_sat order by timestamp) as rn
    from transactions
    where amount_in_sat < 0
    and owner_uuid != ''
),

joined as (select
    o.owner_uuid as owner_uuid,
    o.timestamp as init_timestamp,
    i.timestamp as end_timestamp,
    o.amount_in_sat as amount_in_sat
from outputs_w_rn o
left join inputs_w_rn i
on o.owner_uuid = i.owner_uuid
and o.amount_in_sat = - i.amount_in_sat
and o.rn = i.rn),

w_time_diffs as (
     select
    *,
    (julianday(coalesce(end_timestamp, date('2024-03-29'))) - julianday(init_timestamp)) as diff_days
    from joined
)

select
    owner_uuid,
    sum(amount_in_sat) as total_incoming,
    sum(diff_days * amount_in_sat) / sum(amount_in_sat) as pooled_retention_avg
from w_time_diffs
group by 1
'''

cursor.execute(query)
res = cursor.fetchall()
# df = pd.DataFrame(res, columns=['owner_uuid', 'amount_in_sat','timestamp'])
# owner_uuids = df.owner_uuid.unique()

# for owner_uuid in owner_uuids:
#     owner_df = df.query(f'owner_uuid == \'{owner_uuid}\'').sort_values('timestamp')
#     unspent = []
#     for _, row in owner_df.iterrows():
#         if row['amount_in_sat'] > 0:
#             unspent.append((row['timestamp']))
        
    

In [145]:
pd.DataFrame(res, columns=['owner_uuid', 'total_incoming', 'pooled_retention_avg']).to_csv('retention.csv')

In [146]:
df = pd.DataFrame(res, columns=['owner_uuid', 'total_incoming', 'pooled_retention_avg'])

In [147]:
df

owner_uuid  total_incoming  \
0        0000056f-3d56-4ffc-82d9-16e2dc83f86e            5606   
1        00000747-39ed-4e16-90dc-2908c19888cc           11770   
2        00001111-0d62-4f89-9ea1-738c964b3fc0            5659   
3        00001188-659e-4171-b1de-5fbf216c7119            5606   
4        000023bc-7189-44ae-ae13-78bbdf9800c5           11820   
...                                       ...             ...   
1231342  ffffe9b3-3eb1-481b-aff6-fe32260bff61           30000   
1231343  ffffed51-bfa5-44c2-b364-2f68c6453c9e          274408   
1231344  fffff8a9-5048-4173-bbc9-a52106b0da80            5606   
1231345  fffff995-4601-477a-a66e-a7910097ff84        24346459   
1231346  fffffe43-c325-49cb-8952-ac019e2317a8            5606   

         pooled_retention_avg  
0                    1.190050  
1                    2.909113  
2                    0.273991  
3                    2.223507  
4                    0.129713  
...                       ...  
1231342            110.392593  
1231343            164.512134  
1231344              0.837334  
1231345            511.775625  
1231346              1.870519  

[1231347 rows x 3 columns]

In [148]:
df.query('pooled_retention_avg < 0')

Empty DataFrame
Columns: [owner_uuid, total_incoming, pooled_retention_avg]
Index: []

In [159]:
MIN_INCOMING = 0.01 * BTC_TO_SAT
filt = df.query(f'total_incoming > {MIN_INCOMING}')
filt['log1p_days'] = np.log1p(filt['pooled_retention_avg'])
fig = px.histogram(filt, x='pooled_retention_avg')
fig.update_layout(template='plotly_white', xaxis_title='Pooled average of holding times in days (only considering users that moved more than 0.01 BTC)', yaxis_title='Number of users')




/var/folders/zk/2q0b4dlj1wx42nz9qf6qxqjc0000gq/T/ipykernel_75687/1335903783.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Active users (i.e. users that generated anaytics events)

In [160]:
# We are considering all users that generated at least one event each month.
# Dataset was generated with the following BigQuery:
# '''
# select distinct user_id, DATE_TRUNC(DATE(TIMESTAMP_MICROS(event_timestamp)), MONTH) as month
# from (select * from `muun-58bf8.analytics_151919984.events_2023*` union all select * from `muun-58bf8.analytics_151919984.events_2024*`)
# '''

# Here we should remove the fraudulent users
filtered_out_users = [] # TODO: add fraudulent users
df = pd.read_csv('/Users/gchebi/Downloads/bq-results-20240329-150949-1711725023709.csv')
df = df[~df.user_id.isin(filtered_out_users)]
agg_results = df.groupby('month').agg(num_users = pd.NamedAgg('user_id', 'count')).reset_index()
fig = px.line(agg_results, x = 'month', y = 'num_users')
fig.update_layout(yaxis_title="Number of active users", yaxis_range = [0, 500000], xaxis_title="Date", template='plotly_white')

/var/folders/zk/2q0b4dlj1wx42nz9qf6qxqjc0000gq/T/ipykernel_75687/4085208506.py:10: DtypeWarning:

Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.

